In [279]:
import re
import json
import pickle as pk
from random import randint
from datetime import datetime
from IPython.display import display, clear_output

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt
import plotly
import plotly.express as px
import plotly.graph_objs as go

import nltk
from nltk.tokenize import word_tokenize
import spacy
nlp = spacy.load("de_core_news_sm")
from spacy.lang.de.stop_words import STOP_WORDS
import snowballstemmer
from HanTa import HanoverTagger as ht
 
from sklearn.cluster import MiniBatchKMeans, KMeans
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA, TruncatedSVD
from sklearn.metrics import adjusted_rand_score

import statsmodels

In [2]:
with open("articles.json", "r") as f:
    articles = json.load(f)

In [3]:
articles

[{'article_url': 'https://www.heise.de/news/Telekom-und-Apple-starten-Augmented-Reality-Innovationsprogramm-6147126.html',
  'number_comments': 0,
  'date': '07-26-2021, 16:01',
  'brandig': ['Mac & i'],
  'related_topics': ['5G',
   'Apple',
   'Augmented Reality',
   'Deutsche Telekom',
   'Innovation',
   'iOS',
   'iPhone',
   'Mobilfunk',
   'Startups',
   'Wettbewerb'],
  'authors': ['Ben Schwan'],
  'heading': 'Telekom und Apple starten Augmented-Reality-Innovationsprogramm',
  'lead': 'Im Rahmen des Start-up-Inkubators "Hubraum" können sich Entwickler in sechs Kategorien bewerben, um Apples AR-Technik mit 5G und Co. zu kombinieren.',
  'atricle_text': 'Die Deutsche Telekom AG hat zusammen mit ihrer US-Tochter T-Mobile sowie Apple ein Innovationsprogramm für Augmented Reality (AR) aufgelegt. Die Kampagne läuft im Rahmen des Telekom-Inkubators Hubraum mit Sitz in Deutschland und ist international angelegt. Bewerbungen sind noch bis zum 4. August möglich, danach wird es für die in

# Zewck und Aufbau des Notebooks

tbd
Ziele:
Eigenes Clustering
Verwandte Artikel finden
Überwachtes Lernen finden des

# Clustering anhand der Kurzbeschreibung (lead)

## Vorverarbeitung

### Tokenisierung und Bereinigung

In [3]:
lead_article = [article["lead"] for article in articles]

In [4]:
# removing stopwords
lead_list = []
for lead in lead_article:
    lead_tokens = nltk.word_tokenize(lead)
    lead = " ".join([w for w in lead_tokens if not w.lower() in STOP_WORDS])
    lead = re.sub(r'[^\w]', ' ', lead)
    lead = re.sub(r'[0-9]+', '', lead)
    # remove all multiple white spaces
    lead_list.append(" ".join(lead.split()))

### Stemming 


In [5]:
# Stemming
lead_list_stemming =[]

stemmer = snowballstemmer.stemmer('german') #PorterStemmer()

lead_list_stem = [" ".join(stemmer.stemWords(nltk.word_tokenize(lead))) for lead in lead_list]
  
#for lead in lead_list:
    #lead_nltk_tokens = nltk.word_tokenize(lead)
    #lead_list_stemming.append(" ".join(stemmer.stemWords(token)))
    #for w in lead_nltk_tokens:
     #  print ("Actual: %s  Stem: %s"  % (w,stemmer.stem(w)))

### Lemmatisierung

In [6]:
# Lemmatisierung
#lemmatizer =ht.HanoverTagger('morphmodel_ger.pgz') #WordNetLemmatizer()
lead_list_lemma = []
for lead in lead_list:
    lead_list_lemma.append(" ".join([token.lemma_ for token in nlp(lead)]))

# lemma_list =[]     
# lead_list_lemma = []
# for lead in lead_list:
#     lead_nltk_tokens = nltk.word_tokenize(lead)
#     for w in lead_nltk_tokens:
#       print ("Actual: %s  Lemma: %s"  % (w,lemmatizer.analyze(w)))
#       lemma = lemmatizer.analyze(w) #wordnet_lemmatizer.lemmatize(w)
#       lemma_list.append(lemma[0])
#     lemmas = ' '.join(map(str,lemma_list))
#     lead_list_lemma.append(lemmas)
#     lemma_list = []

### Vektorisierung

In [213]:
lead_lemma_vectorizer = TfidfVectorizer()
lead_lemma_tfidf = lead_lemma_vectorizer.fit_transform(lead_list_lemma)

lead_stem_vectorizer = TfidfVectorizer()
lead_stem_tfidf = lead_stem_vectorizer.fit_transform(lead_list_stem)

In [8]:
pd.DataFrame(lead_lemma_tfidf.toarray(), columns=lead_lemma_vectorizer.get_feature_names())

aabenraa  aachen  aachener  aalglatt  aargau  abarbeiten  abb  abbau  \
0           0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
1           0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
2           0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
3           0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
4           0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
...         ...     ...       ...       ...     ...         ...  ...    ...   
13626       0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
13627       0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
13628       0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
13629       0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   
13630       0.0     0.0       0.0       0.0     0.0         0.0  0.0    0.0   

       abbauen  abbestellungen  ...  überziehen  üblich  üblicherweise  übrig  \
0          0.0             0.0  ...         0.0     0.0            0.0    0.0   
1          0.0             0.0  ...         0.0     0.0            0.0    0.0   
2          0.0             0.0  ...         0.0     0.0            0.0    0.0   
3          0.0             0.0  ...         0.0     0.0            0.0    0.0   
4          0.0             0.0  ...         0.0     0.0            0.0    0.0   
...        ...             ...  ...         ...     ...            ...    ...   
13626      0.0             0.0  ...         0.0     0.0            0.0    0.0   
13627      0.0             0.0  ...         0.0     0.0            0.0    0.0   
13628      0.0             0.0  ...         0.0     0.0            0.0    0.0   
13629      0.0             0.0  ...         0.0     0.0            0.0    0.0   
13630      0.0             0.0  ...         0.0     0.0            0.0    0.0   

       übrigen  übung  üppig  šefčovič  škoda  škodas  
0          0.0    0.0    0.0       0.0    0.0     0.0  
1          0.0    0.0    0.0       0.0    0.0     0.0  
2          0.0    0.0    0.0       0.0    0.0     0.0  
3          0.0    0.0    0.0       0.0    0.0     0.0  
4          0.0    0.0    0.0       0.0    0.0     0.0  
...        ...    ...    ...       ...    ...     ...  
13626      0.0    0.0    0.0       0.0    0.0     0.0  
13627      0.0    0.0    0.0       0.0    0.0     0.0  
13628      0.0    0.0    0.0       0.0    0.0     0.0  
13629      0.0    0.0    0.0       0.0    0.0     0.0  
13630      0.0    0.0    0.0       0.0    0.0     0.0  

[13631 rows x 26785 columns]

In [9]:
pd.DataFrame(lead_stem_tfidf.toarray(), columns=lead_stem_vectorizer.get_feature_names())

aabenraa  aach  aalglatt  aargau  abb  abbau  abbestell  abbieg  \
0           0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
1           0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
2           0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
3           0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
4           0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
...         ...   ...       ...     ...  ...    ...        ...     ...   
13626       0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
13627       0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
13628       0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
13629       0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   
13630       0.0   0.0       0.0     0.0  0.0    0.0        0.0     0.0   

       abbiegeassistent  abbild  ...  überweisungsgebuhr  überweisungstag  \
0                   0.0     0.0  ...                 0.0              0.0   
1                   0.0     0.0  ...                 0.0              0.0   
2                   0.0     0.0  ...                 0.0              0.0   
3                   0.0     0.0  ...                 0.0              0.0   
4                   0.0     0.0  ...                 0.0              0.0   
...                 ...     ...  ...                 ...              ...   
13626               0.0     0.0  ...                 0.0              0.0   
13627               0.0     0.0  ...                 0.0              0.0   
13628               0.0     0.0  ...                 0.0              0.0   
13629               0.0     0.0  ...                 0.0              0.0   
13630               0.0     0.0  ...                 0.0              0.0   

       überwind  überzeug  überzeugungsarbeit  übrig  übung  šefčovič  škoda  \
0           0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
1           0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
2           0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
3           0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
4           0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
...         ...       ...                 ...    ...    ...       ...    ...   
13626       0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
13627       0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
13628       0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
13629       0.0       0.0                 0.0    0.0    0.0       0.0    0.0   
13630       0.0       0.0                 0.0    0.0    0.0       0.0    0.0   

       škodas  
0         0.0  
1         0.0  
2         0.0  
3         0.0  
4         0.0  
...       ...  
13626     0.0  
13627     0.0  
13628     0.0  
13629     0.0  
13630     0.0  

[13631 rows x 24257 columns]

## Finden der besten Cluster-Anzahl

### Finden der besten Cluster-Anzahl mittels Lemma- und Stemming-Vektor
Das Iterieren über die verschiedene Cluseranzahlen dauert sehr lange (ca. 6h um 1 bis 100 Cluster zu durchsuchen; Tendenz steigend). Deshalb wird im folgenden eine "feine Suche" zwischen 1 und 100 Clustern mit dem normalen KMeans durchgefürht und eine "grobe Suche" zwischen 1 und 300 Clustern mit dem MiniBatchKMeans durchgefürht.<br> Da man bei der explorativen Analyse gesehen hat, dass 90% der Artikel eines der 265 häufigsten Themen zugewiesen werden kann, scheint eine Obergrenze der Analyse von 300 Clustern als sinnvoll. Außerdem hat die explorative Analyse gezeigt, dass über die Hälfte der 913 Unterthemen oder kaum unterscheidbar von anderen Themen sind.

In [97]:
# distortions = []
K = range(1,300)
# for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = MiniBatchKMeans(n_clusters=k,random_state=42, n_init=10, batch_size=1000)
#     kmeanModel.fit(lead_lemma_tfidf)
#     distortions.append(kmeanModel.inertia_)

# pk.dump(distortions, open("lead_lemma_distortions_300.pkl","wb"))

distortions = pk.load(open("lead_lemma_distortions_300.pkl",'rb'))

trendline = px.scatter(x=K, y=distortions, trendline="ols", trendline_options=dict(log_x=True),trendline_scope="overall")

fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.add_trace(trendline.data[1])
fig.show()

Mittels der Ellenbogen-Methode lässt sich bei ca. 40 Clustern ein "Ellenbogen" erkennen, da die Steigung danach signifikant weniger wird.

In [92]:
# Dauer 5:54 Stunden
# distortions = []
K = range(1,100)
# for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = KMeans(n_clusters=k,random_state=42)
#     kmeanModel.fit(lead_lemma_tfidf)
#     distortions.append(kmeanModel.inertia_)
# pk.dump(distortions, open("lead_lemma_distortions.pkl","wb"))

distortions = pk.load(open("lead_lemma_distortions.pkl",'rb'))



fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.show()

Mit der Ellenbogen-Methode lässt sich kein eindetiger Ellenbogen feststellen. Wie oben dargestellt lässt sich aber bei ca. 50 ein solcher Punkt feststellen.

In [98]:
distortions = []
K = range(1,300)
# for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = MiniBatchKMeans(n_clusters=k,random_state=42, n_init=10, batch_size=1000)
#     kmeanModel.fit(lead_stem_tfidf)
#     distortions.append(kmeanModel.inertia_)
    
# pk.dump(distortions, open("lead_stem_distortions_300.pkl","wb"))

distortions = pk.load(open("lead_stem_distortions_300.pkl",'rb'))
    
trendline = px.scatter(x=K, y=distortions, trendline="ols", trendline_options=dict(log_x=True),trendline_scope="overall")

fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.add_trace(trendline.data[1])
fig.show()

Im vergleich zur Lemmatisierung lässt sich hier ein ähnliches Bild feststellen.

In [100]:
# Dauer 5:45 Stunden
# distortions = []
K = range(1,100)
# for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = KMeans(n_clusters=k,random_state=42)
#     kmeanModel.fit(lead_stem_tfidf)
#     distortions.append(kmeanModel.inertia_)
# pk.dump(distortions, open("lead_stem_distortions.pkl","wb"))

distortions = pk.load(open("lead_stem_distortions.pkl",'rb'))

fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.show()

Durch Stemming ergibt sich ein ähnliches Bild. Da die Lemmas aber einfacher verständlich sind, wird im Folgenden vorerst mit den Lemmas weiter experimentiert.

### PCA zur Dimensionalitätsreduktion
Da es in den Daten mehr Features als Featurevektoren gibt und somit der Fluch der Dimensionalität einer sehr große Rolle spielt, wird mittels PCA versucht die Anzahl der Features zu reduzieren.  

In [14]:
# Initiale Berechnung 40min; kann nun aus einer Datei geladen werden
#lead_lemma_pca = PCA().fit(lead_lemma_tfidf.toarray())
#pk.dump(pca, open("lead_lemma_pca.pkl","wb"))
lead_lemma_pca = pk.load(open("lead_lemma_pca.pkl",'rb'))

In [15]:
explained_variance = np.cumsum(lead_lemma_pca.explained_variance_ratio_)
fig = px.area(
    x=range(1, explained_variance.shape[0] + 1),
    y=explained_variance,
    labels={"x": "# Components", "y": "Explained Variance"}
)
fig.show()
# Um Speicherplatz nicht zu überlasten
del lead_lemma_pca

Bereits ca. 4710 Hauptkomponenten erklären 80 % der Varianz. Im Folgenden werden deshalb diese Hauptkomponenten verwendent, um die Dimensionalität zu reduzieren.

In [16]:
n_components = list(explained_variance > 0.8).index(True) # Schneller als n_components auf 0.8 zu setzen

In [17]:
#lead_lemma_pca_80 = PCA(n_components=n_components, random_state=42)
#lead_lemma_pca_80_features = lead_lemma_pca_80.fit_transform(lead_lemma_tfidf.toarray())
#pk.dump(lead_lemma_pca_80, open("lead_lemma_pca_80.pkl","wb"))
#print(lead_lemma_pca_80_features.shape)
lead_lemma_pca_80 = pk.load(open("lead_lemma_pca_80.pkl",'rb'))
lead_lemma_pca_80_features = lead_lemma_pca_80.transform(lead_lemma_tfidf.toarray())
# Um Speicherplatz nicht zu überlasten
del lead_lemma_pca_80

In [267]:
#distortions = []
K = range(1,300)
#for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = MiniBatchKMeans(n_clusters=k,random_state=42, n_init=10, batch_size=1000)
#     kmeanModel.fit(lead_lemma_pca_80_features)
#     distortions.append(kmeanModel.inertia_)

# pk.dump(distortions, open("lead_pca_distortions_300.pkl","wb"))

distortions = pk.load(open("lead_pca_distortions_300.pkl",'rb'))
    
trendline = px.scatter(x=K, y=distortions, trendline="ols", trendline_options=dict(log_x=True),trendline_scope="overall")

fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.add_trace(trendline.data[1])
fig.show()

Auch im Falle der PCA ergibt sich ein ähnliches Bild.

In [104]:
# distortions = []
# K = range(1,100)
# for k in K:
#     clear_output(wait=True)
#     display(f"Iteration {k}")
#     kmeanModel = KMeans(n_clusters=k, random_state=42)
#     kmeanModel.fit(lead_lemma_pca_80_features)
#     distortions.append(kmeanModel.inertia_)

# pk.dump(distortions, open("lead_pca_distortions.pkl","wb"))

distortions = pk.load(open("lead_pca_distortions.pkl",'rb'))
    
fig = go.Figure()
fig.add_trace(go.Scatter(x=list(K), y=distortions,
                    mode='lines+markers'))
fig.show()

Durch vorherige Dimensionalitätsreduktion der Daten mittels PCA scheint sich kein eindeutiger Vorteil bzw. kein eindeutigerens Clustering zu ergeben. Deshalb wird mit der einfachsten Lösung des lemmatisierten TFIDF-Vektors und 50 Clustern fortgefahren. 

### LSA zur Dimensionalitätreduktion
Die LSA ist wie die PCA ebenfalls zur linearen Dimensionalitätsreduktion geeignet. LSA ist besonders für "sparse"-Matrizen wie die TFIDF-Matrix geeignet. [1]

[1] https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.TruncatedSVD.html

In [277]:
lead_lemma_tfidf

<13631x26785 sparse matrix of type '<class 'numpy.float64'>'
	with 152284 stored elements in Compressed Sparse Row format>

In [ ]:
svd = TruncatedSVD(26784)
df = svd.fit_transform(lead_lemma_tfidf)

#normalizer = Normalizer(copy=False)
#lsa = make_pipeline(svd, normalizer)

#svd.explained_variance_ratio_.sum()

#X = lsa.fit_transform(X)

In [214]:
del lead_stem_vectorizer
del lead_stem_tfidf

## Finales Clustering + Analyse

In [270]:
# true_k = 40
# lemma_kmeans_model = KMeans(n_clusters=true_k,random_state=42, n_init=20, max_iter=500)
# lemma_kmeans_model.fit(lead_lemma_tfidf)

# pk.dump(lemma_kmeans_model, open("lemma_kmeans_model.pkl","wb"))

lemma_kmeans_model = pk.load(open("lemma_kmeans_model.pkl",'rb'))

In [ ]:
## Wichtigste Worte gemäß TFIDF


In [273]:
print("Top terms per cluster:")
order_centroids = lemma_kmeans_model.cluster_centers_.argsort()[:, ::-1]
terms = lead_lemma_vectorizer.get_feature_names()
for i in range(40):
    print("Cluster %d:" % i),
    for ind in order_centroids[i, :10]:
        print(' %s' % terms[ind]),

Top terms per cluster:
Cluster 0:
 dollar
 us
 amerikanischen
 milliarde
 million
 apple
 quartal
 gewinn
 iphone
 wert
Cluster 1:
 hersteller
 iphone
 deutsch
 apple
 auto
 smartphone
 chinesische
 chinesisch
 smartphones
 laut
Cluster 2:
 china
 usa
 huawei
 handelskrieg
 apple
 europa
 amerikanischen
 us
 markt
 peking
Cluster 3:
 apple
 sehen
 app
 künftig
 chef
 firma
 kunde
 laut
 it
 usa
Cluster 4:
 antrieb
 elektrisch
 rein
 fahren
 angetrieben
 auto
 lkw
 betrieben
 mercedes
 alternative
Cluster 5:
 amazon
 verdi
 mitarbeiter
 händler
 gewerkschaft
 bezos
 prime
 jeff
 onlinehändler
 streik
Cluster 6:
 zeigen
 digitalisierung
 unternehmen
 umfrage
 elektroauto
 zahl
 aktuell
 deutschland
 pandemie
 cebit
Cluster 7:
 internet
 united
 ding
 schnell
 drillisch
 rocket
 schnelles
 unternehmen
 kunde
 satellit
Cluster 8:
 umsatz
 prozent
 quartal
 gewinn
 steigern
 steigen
 deutlich
 sinken
 aktie
 anleger
Cluster 9:
 bmw
 daimler
 auto
 modell
 ix
 vw
 suv
 fahren
 kunde
 bekomme

### Einordnen von Texten in die Cluster

In [ ]:
print("\n")
print("Prediction")
Y = vectorizer.transform(["Das neue I-Phone ist da"])
prediction = model.predict(Y)
print(prediction)

Y = vectorizer.transform(["Der amerikanische Präsident Trump hat Milliarden an US-Dollar verschwendet"])
prediction = model.predict(Y)
print(prediction)

# Visualization

### 2D Plot

In [ ]:
# reduce the features to 2D
pca = PCA(n_components=2, random_state=0)
reduced_features = pca.fit_transform(X.toarray())

# reduce the cluster centers to 2D
reduced_cluster_centers = pca.transform(model.cluster_centers_)

In [ ]:
plt.scatter(reduced_features[:,0], reduced_features[:,1], c=model.predict(X))
plt.scatter(reduced_cluster_centers[:, 0], reduced_cluster_centers[:,1], marker='x', s=150, c='b')

### 3D Plot

In [ ]:
# reduce the features to 3D
pca_1 = PCA(n_components=3, random_state=0)
reduced_features_1 = pca_1.fit_transform(X.toarray())

# reduce the cluster centers to 2D
reduced_cluster_centers_1 = pca_1.transform(model.cluster_centers_)

In [ ]:
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt



fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')

x = reduced_features_1[:,0]
y = reduced_features_1[:,1]
z = reduced_features_1[:,2]

ax.scatter(x, y, z, c=model.predict(X), marker='o')

ax.set_xlabel('X Label')
ax.set_ylabel('Y Label')
ax.set_zlabel('Z Label')

plt.show()

### 3D Plot interactive

In [ ]:
# Configure Plotly to be rendered inline in the notebook.
plotly.offline.init_notebook_mode()
# Configure the trace.
trace = go.Scatter3d(
    x = reduced_features_1[:,0],
    y = reduced_features_1[:,1],
    z = reduced_features_1[:,2], # <-- Put your data instead
    #surfacecolor= 'purple',
    mode='markers',
    #mode =prediction_list,  
    marker={
        'size': 10,
        'opacity': 0.8,
        'color': model.predict(X)
    }
    
)
# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
   
)
data = [trace]
 
plot_figure = go.Figure(data=data, layout=layout)
# Render the plot.
plotly.offline.iplot(plot_figure)

Es zeigt sich, dass die meisten Artikel vier verschiedenen Clustern zugeordnet werden können. Nach diesem Bild macht es keinen Sinn mehr als maximal 5 Cluster zu verwenden, jedoch zeigt sich im foolgenden Abschnitt eine interessante Besonderheit. 

## Veränderung über die Zeit betrachten 

In [ ]:
labels = model.labels_
df= pd.DataFrame(lead_list_lemma, columns = ['lead'])
df['label'] = labels
df

In [ ]:
date = [[datetime.strptime(article["date"], "%m-%d-%Y, %H:%M").year, datetime.strptime(article["date"], "%m-%d-%Y, %H:%M").month] for article in articles]
date_df= pd.DataFrame(date, columns =['year','month'])
horizontal_concat = pd.concat([df, date_df], axis=1)

In [ ]:
horizontal_concat

In [ ]:
year_label_freq_df = horizontal_concat.groupby(['year','label']).size().groupby('year', group_keys=False).nlargest(5).reset_index(name="frequency")
# Nur die Jahre 2017 bis 2021
year_label_freq_df = year_label_freq_df[year_label_freq_df.year.isin(range(2017,2022))]

In [ ]:
year_label_freq_pivot = year_label_freq_df.pivot(index="year",columns="label", values="frequency")
#Sortieren nach NaN Werten, um besseren Barplot zu erhalten
year_label_freq_pivot = year_label_freq_pivot[year_label_freq_pivot.isnull().sum().sort_values(ascending=True).index]

In [ ]:
fig, ax = plt.subplots(figsize=(20,10))
year_label_freq_pivot.plot.bar(stacked=True, ax=ax)
plt.show()

Hier zeigt sich, dass der Cluster Nummer 5 erst ab 2020 auftritt, sowie der Cluster Nummer 3 nur bis zum Jahr 2019. Der Cluster Nummer 5 mit den Schlagwörtern: 
-  corona
-  pandemie
-  krise
-  coronavirus
-  homeoffice
-  profitieren
-  deutschland
-  online
-  covid
-  deutsch

lässt sich eindeutig der Conrona Pandemie zuornen. 

## überwachtes Lernen 

# Clustering atricle_text

In [ ]:
text_article = [article["atricle_text"] for article in articles]
text_article

In [ ]:
# removing stopwords
stopwords = STOP_WORDS 
pattern = re.compile(r'\b(' + r'|'.join(stopwords) + r')\b\s*')
text_list = []
for i, text in enumerate(text_article):
    text = pattern.sub('', text)
    text = re.sub(r'[^\w]', ' ', text)
    text = re.sub(r'[0-9]+', '', text)
    text_list.append(text)
 
text_list  

In [ ]:
# Lemmatisierung
lemmatizer =ht.HanoverTagger('morphmodel_ger.pgz') #WordNetLemmatizer()
       
lemma_list =[]     
text_list_lemma = []
for i, text in enumerate(text_list):
    text_nltk_tokens = nltk.word_tokenize(text)
    for w in text_nltk_tokens:
      print ("Actual: %s  Lemma: %s"  % (w,lemmatizer.analyze(w)))
      lemma = lemmatizer.analyze(w)
      lemma_list.append(lemma[0])
    lemmas = ' '.join(map(str,lemma_list))
    text_list_lemma.append(lemmas)
    lemma_list = []

In [ ]:
text_list_lemma

In [ ]:
# Clustering with Kmeans 
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from sklearn.metrics import adjusted_rand_score

documents = lead_list_lemma

vectorizer = TfidfVectorizer(stop_words=adv.stopwords['german'])
X = vectorizer.fit_transform(documents)

true_k = 6
model = KMeans(n_clusters=true_k, init='k-means++', max_iter=100, n_init=50)
model.fit(X)

print("Top terms per cluster:")
order_centroids = model.cluster_centers_.argsort()[:, ::-1]
terms = vectorizer.get_feature_names()
for i in range(true_k):
    print("Cluster %d:" % i),
    for ind in order_centroids[i, :10]:
        print(' %s' % terms[ind]),
    print

In [ ]:
# reduce the features to 3D
pca_1 = PCA(n_components=3, random_state=0)
reduced_features_1 = pca_1.fit_transform(X.toarray())

# reduce the cluster centers to 2D
reduced_cluster_centers_1 = pca_1.transform(model.cluster_centers_)

In [ ]:
plotly.offline.init_notebook_mode()
# Configure the trace.
trace = go.Scatter3d(
    x = reduced_features_1[:,0],
    y = reduced_features_1[:,1],
    z = reduced_features_1[:,2], # <-- Put your data instead
    #surfacecolor= 'purple',
    mode='markers',
    #mode =prediction_list,  
    marker={
        'size': 10,
        'opacity': 0.8,
        'color': model.predict(X)
    }
    
)
# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0}
   
)
data = [trace]
 
plot_figure = go.Figure(data=data) #, layout=layout)
# Render the plot.
plotly.offline.iplot(plot_figure)

Auch hier ist deutlich zu sehen, dass 4 bis 5 Cluster maximal ausreichen um die Texte zu gruppieren. 
... Label welche Farbe ist welcher Cluster? 

In [ ]:
labels = model.labels_
df= pd.DataFrame(text_list_lemma, columns = ['text'])
df['label'] = labels

In [ ]:
date = [[datetime.strptime(article["date"], "%m-%d-%Y, %H:%M").year, datetime.strptime(article["date"], "%m-%d-%Y, %H:%M").month] for article in articles]
date_df= pd.DataFrame(date, columns =['year','month'])
horizontal_concat = pd.concat([df, date_df], axis=1)

In [ ]:
year_label_freq_df = horizontal_concat.groupby(['year','label']).size().groupby('year', group_keys=False).nlargest(5).reset_index(name="frequency")
# Nur die Jahre 2017 bis 2021
year_label_freq_df = year_label_freq_df[year_label_freq_df.year.isin(range(2017,2022))]

In [ ]:
year_label_freq_pivot = year_label_freq_df.pivot(index="year",columns="label", values="frequency")
#Sortieren nach NaN Werten, um besseren Barplot zu erhalten
year_label_freq_pivot = year_label_freq_pivot[year_label_freq_pivot.isnull().sum().sort_values(ascending=True).index]

In [ ]:
fig, ax = plt.subplots(figsize=(20,10))
year_label_freq_pivot.plot.bar(stacked=True, ax=ax)
plt.show()

# Ähnlichste Artikel finden 

In [ ]:
documents = lead_list_lemma

vectorizer = TfidfVectorizer(stop_words=stopwords)
X = vectorizer.fit_transform(documents)

pairwise_similarity = X * X.T

In [ ]:
pairwise_similarity = X * X.T

arr = pairwise_similarity.toarray()     
np.fill_diagonal(arr, np.nan) 

In [ ]:
input_idx = randint(0,len(lead_list_lemma))
result_idx = np.nanargmax(arr[input_idx])                                                                                                                                                                                                                
print('Input: \n' + lead_article[input_idx]+ '\n')                                                                                                                                                                                                                                     
print('Output: \n'+ lead_article[result_idx])